In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
# tsl library
!git clone https://github.com/TorchSpatiotemporal/tsl.git
!pip install torch==1.10.1+cu111 torchvision==0.11.2+cu111 torchaudio==0.10.1 -f https://download.pytorch.org/whl/torch_stable.html
!pip install torch-scatter torch-sparse torch-geometric -f https://data.pyg.org/whl/torch-1.10.1+cu113.html
!pip install ./tsl

Cloning into 'tsl'...
remote: Enumerating objects: 629, done.
remote: Counting objects: 100% (110/110), done.
remote: Compressing objects: 100% (45/45), done.
remote: Total 629 (delta 81), reused 80 (delta 65), pack-reused 519
Receiving objects: 100% (629/629), 218.90 KiB | 19.90 MiB/s, done.
Resolving deltas: 100% (341/341), done.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in links: https://download.pytorch.org/whl/torch_stable.html
     |████████████▌                   | 834.1 MB 1.5 MB/s eta 0:14:14tcmalloc: large alloc 1147494400 bytes == 0x396e8000 @  0x7f9c54f46615 0x592b76 0x4df71e 0x59afff 0x515655 0x549576 0x593fce 0x548ae9 0x51566f 0x549576 0x593fce 0x548ae9 0x5127f1 0x598e3b 0x511f68 0x598e3b 0x511f68 0x598e3b 0x511f68 0x4bc98a 0x532e76 0x594b72 0x515600 0x549576 0x593fce 0x548ae9 0x5127f1 0x549576 0x593fce 0x5118f8 0x593dd7
     |███████████████▉                | 1055.7 MB 2.4 MB/s eta 0:07:25tcmalloc: large al

In [3]:
# to check availability of GPU
import tensorflow as tf
devices = tf.config.list_physical_devices('GPU')
print(devices)

tf.test.is_gpu_available()

[PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]
Instructions for updating:
Use `tf.config.list_physical_devices('GPU')` instead.


True

In [4]:
#libraries
import numpy as np
from datetime import datetime
import pandas as pd
import pytorch_lightning as pl
import torch
import tsl

from datetime import datetime
from pytorch_lightning.loggers import TensorBoardLogger
from pytorch_lightning.callbacks import ModelCheckpoint
from tsl.data import SpatioTemporalDataset, SpatioTemporalDataModule
from tsl.data.preprocessing import StandardScaler
from tsl.nn.blocks.encoders import RNN
from tsl.nn.blocks.decoders import GCNDecoder
from tsl.nn.metrics.metrics import MaskedMAE, MaskedMAPE, MaskedMRE, MaskedMSE
from tsl.predictors import Predictor
from tsl.datasets.prototypes import PandasDataset

np.set_printoptions(suppress=True)
tsl.logger.disabled = True

print(f"tsl version  : {tsl.__version__}")
print(f"torch version: {torch.__version__}")

tsl version  : 0.1.0
torch version: 1.10.1+cu111


In [5]:
# display options
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

In [6]:
path = "/content/drive/MyDrive/data/"  # THIS LINE NEEDS TO BE CHANGED BASED ON THE PATH OF THE FILES TO RETRIEVE

# TODO 1: distance matrix
distance = pd.read_csv(f'{path}sf12010countydistancemiles.csv')
distance.head()

county1  mi_to_county  county2
0     1001     22.462994     1021
1     1001     26.844687     1085
2     1001     29.517585     1051
3     1001     30.776371     1047
4     1001     34.493443     1101

In [7]:
print(distance.shape,
      len(distance.county1.unique())) # this will affect the construction of the matrix --> add the distances assuming transititvity of them

(10371620, 3) 3221


In [8]:
# building a symmetric matrix with distances between counties
db_distances = {}
for index, row in distance.iterrows():
  if (int(row['county1']), int(row['county2'])) not in db_distances:
    db_distances[((int(row['county1']), int(row['county2'])))] = row['mi_to_county']
  if (int(row['county2']), int(row['county1'])) not in db_distances:
    db_distances[((int(row['county2']), int(row['county1'])))] = row['mi_to_county']

distance_matrix = pd.DataFrame(db_distances.values(), index=pd.MultiIndex.from_tuples(db_distances.keys())).unstack(1).fillna(0)[0]

In [9]:
distance_matrix.head()

1001        1003        1005        1007        1009        1011   \
1001    0.000000  144.995720   85.807128   43.403253   99.668005   61.910627   
1003  144.995720    0.000000  161.594903  166.832795  239.370845  155.736017   
1005   85.807128  161.594903    0.000000  127.822083  160.398786   24.265804   
1007   43.403253  166.832795  127.822083    0.000000   73.854980  103.585356   
1009   99.668005  239.370845  160.398786   73.854980    0.000000  138.631808   

           1013        1015        1017        1019        1021        1023   \
1001   54.262869   97.701681   77.437126  120.376535   22.462994  101.026274   
1003   98.242292  242.660056  208.485723  265.356767  163.044172   96.684704   
1005   75.399408  133.562044   72.363965  152.608245  102.769275  166.937203   
1007   91.129572   91.601733  100.820598  111.774749   25.777246   96.367215   
1009  153.930616   45.024731   99.752813   52.668701   78.160965  168.327377   

           1025        1027        1029        1031        1033        1035   \
1001   90.429828   67.927367  102.084144   87.271485  163.835297   79.224318   
1003   71.040281  211.368124  245.628293  115.991213  279.424609   69.397615   
1005  142.312522  100.126778  124.624439   47.190402  239.667895   98.194948   
1007  100.389711   75.230518  103.447570  129.832051  122.826843  109.976511   
1009  174.222394   63.640973   63.918748  181.079450   86.438114  177.852106   

           1037        1039        1041        1043        1045        1047   \
1001   35.892759   90.031286   58.691334  111.002110   97.548532   30.776371   
1003  180.087407   86.843791  112.310078  245.329092  137.247660  121.522641   
1005   88.100117   75.149903   54.495583  177.771208   32.684651  105.007358   
1007   51.551745  128.700413  100.407010   78.526140  140.942973   47.151920   
1009   74.642668  188.989765  155.754915   20.318000  184.563942  117.908847   

           1049        1051        1053        1055        1057        1059   \
1001  141.515199   29.517585  102.466312  110.201265  104.561742  148.669412   
1003  285.965992  163.784660   46.843452  254.529234  212.326160  261.424841   
1005  180.447291   66.157139  116.037822  154.769331  187.382380  226.785955   
1007  125.488575   64.069268  130.895116   95.091376   61.235823  106.770296   
1009   54.931170   98.465032  200.390938   30.899196   70.061066   79.638335   

           1061        1063        1065        1067        1069        1071   \
1001  110.876386   79.637327   58.862718  108.302005  123.802704  158.590391   
1003  117.797834  151.530926  144.832781  159.684236  149.251741  301.628311   
1005   59.263671  163.791449  143.117365   26.303087   49.644778  202.585001   
1007  153.329711   49.966138   34.035146  151.261922  167.205953  137.579880   
1009  204.082083  112.332193  104.266056  186.675393  208.368122   63.885651   

           1073        1075        1077        1079        1081        1083   \
1001   71.772304  120.134908  173.516556  143.147626   75.341842  158.297829   
1003  206.057238  217.033378  293.346450  268.566351  194.603382  290.227342   
1005  145.021026  204.383482  246.376225  214.536508   50.765129  222.535461   
1007   39.457361   76.858252  133.872744  105.195270  106.879434  124.258613   
1009   34.870901   88.183648   88.953990   57.563509  117.989234   62.196558   

           1085        1087        1089        1091        1093        1095   \
1001   26.844687   56.427513  154.023671   69.807668  131.710038  123.921075   
1003  121.460393  169.917668  292.005414  109.778034  240.505574  265.516228   
1005   75.422411   39.442100  210.578912  142.098221  212.424097  176.657827   
1007   66.079993   94.030100  125.235172   65.653804   88.876427  100.672323   
1009  126.502438  120.959929   54.369740  138.927819   76.048413   26.903026   

           1097        1099        1101        1103        1105        1107   \
1001  157.192884   78.961095   34.493443  133.037638   38.460869   99.280304   
100

In [10]:
# note that the dimension of the adj matrix is (3234, 3234)
print(distance_matrix.shape, len(distance_matrix.index.unique()))

(3221, 3221) 3221


In [11]:
# path = "/Users/roccofelici/Desktop/GDL_project_COVID/dataset/"  # THIS LINE NEEDS TO BE CHANGED BASED ON THE PATH OF THE FILES TO RETRIEVE

# Import the adjacency matrix (includes an edge between counties whithin 50 miles and counties "adjacent by air") and set the FIPS as index 
adj_df = pd.read_csv(f'{path}adjacency_matrix.csv')
adj_df.set_index('--', inplace=True)

In [12]:
adj_df.head() # shape: (3234, 3234)

1001  1003  1005  1007  1009  1011  1013  1015  1017  1019  1021  1023  \
--                                                                             
1001   0.0   0.0   0.0   1.0   0.0   0.0   0.0   0.0   0.0   0.0   1.0   0.0   
1003   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1005   0.0   0.0   0.0   0.0   0.0   1.0   0.0   0.0   0.0   0.0   0.0   0.0   
1007   1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   1.0   0.0   
1009   0.0   0.0   0.0   0.0   0.0   0.0   0.0   1.0   0.0   0.0   0.0   0.0   

      1025  1027  1029  1031  1033  1035  1037  1039  1041  1043  1045  1047  \
--                                                                             
1001   0.0   0.0   0.0   0.0   0.0   0.0   1.0   0.0   0.0   0.0   0.0   1.0   
1003   1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1005   0.0   0.0   0.0   1.0   0.0   0.0   0.0   0.0   0.0   0.0   1.0   0.0   
1007   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   1.0   
1009   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   1.0   0.0   0.0   

      1049  1051  1053  1055  1057  1059  1061  1063  1065  1067  1069  1071  \
--                                                                             
1001   0.0   1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1003   0.0   0.0   1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1005   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   1.0   1.0   0.0   
1007   0.0   0.0   0.0   0.0   0.0   0.0   0.0   1.0   1.0   0.0   0.0   0.0   
1009   0.0   0.0   0.0   1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   

      1073  1075  1077  1079  1081  1083  1085  1087  1089  1091  1093  1095  \
--                                                                             
1001   0.0   0.0   0.0   0.0   0.0   0.0   1.0   0.0   0.0   0.0   0.0   0.0   
1003   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1005   0.0   0.0   0.0   0.0   0.0   0.0   0.0   1.0   0.0   0.0   0.0   0.0   
1007   1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1009   1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   1.0   

      1097  1099  1101  1103  1105  1107  1109  1111  1113  1115  1117  1119  \
--                                                                             
1001   0.0   0.0   1.0   0.0   1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1003   1.0   1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1005   0.0   0.0   0.0   0.0   0.0   0.0   1.0   0.0   1.0   0.0   0.0   0.0   
1007   0.0   0.0   0.0   0.0   1.0   0.0   0.0   0.0   0.0   0.0   1.0   0.0   
1009   0.0   0.0   0.0   1.0   0.0   0.0   0.0   0.0   0.0   1.0   1.0   0.0   

      1121  1123  1125  1127  1129  1131  1133  2013  2016  2020  2050  2060  \
--                                                                             
1001   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1003   0.0   0.0   0.0   0.0   1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1005   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1007   0.0   0.0   1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1009   1.0   0.0   0.0   1.0   0.0   0.0   1.0   0.0   0.0   0.0   0.0   0.0   

      2068  2070  2090  2100  2105  2110  2122  2130  2150  2164  2170  2180  \
--                                                                             
1001   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1003   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1005   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1007   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1009   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   

      2185  2188  2195  2198  2220  2230  2240  2261  2270  2275  2282  2290  \

In [13]:
# missing data in the distance matrix
list_indexes1 = set(distance_matrix.index.tolist())
print(len(list_indexes1))

list_indexes2 = set(adj_df.index.tolist())
print(len(list_indexes2))

print("-------")
for el in list_indexes2:
  if el not in list_indexes1:
    print(el)

# the set of distances does not include the following fips
# --> we will set these counties as non adjacent to the other 

3221
3234
-------
66010
60010
60020
60030
60040
60050
69085
69100
69110
69120
78010
78020
78030


In [14]:
# function for the union of two dictionary excluding duplicates
def union_dict(d1, d2):
  union = d1.copy()
  for i in d1:
    for j in d2:
      if i == j:
        union[i] = list(set(d1[i] + d2[j]))
        break
  return union

In [15]:
# path = "/Users/roccofelici/Desktop/GDL_project_COVID/dataset/"  # THIS LINE NEEDS TO BE CHANGED BASED ON THE PATH OF THE FILES TO RETRIEVE

# import: the dataset including the adjacency between counties - the dataset of distances between counties whithin 50 miles - the dataset of "air adjacencies"
adj_county = pd.read_csv (f'{path}county_adjacency2010.csv')
county_dist = pd.read_csv (f'{path}sf12010countydistance50miles.csv')
air_mobility = pd.read_csv(f'{path}air_mobility.csv')

In [16]:
# Create dictionary with adjacency county
county_dict = {}
for index, row in adj_county.iterrows():
  if row['fipscounty'] not in county_dict:
    county_dict[row['fipscounty']] = [int(row['fipsneighbor'])]
  else:
    county_dict[row['fipscounty']].append(int(row['fipsneighbor']))

for i in county_dict:
  county_dict[i].remove(i)

# Create dictionary with county with a maximum distance of 50 miles
dist_county_dict = {}
for index, row in county_dist.iterrows():
  if row['county1'] not in dist_county_dict:
    dist_county_dict[row['county1']] = [int(row['county2'])]
  else:
    dist_county_dict[row['county1']].append(int(row['county2']))

air = {}
for index, row in air_mobility.iterrows():
  if row['dest_fips'] not in air:
    air[row['dest_fips']] = [int(row['origin_fips'])]
  else:
    air[row['dest_fips']].append(int(row['origin_fips']))

In [17]:
# Make the union with the three dictionaries
adj_dict = union_dict(county_dict, dist_county_dict)
adj_dict = union_dict(adj_dict, air)

In [18]:
# Create the adjacency matrix
adj = np.zeros((len(adj_dict), len(adj_dict)))
# Create a list containing all the fips of all county
list_keys = list(adj_dict.keys())

# Fill the adjacency matrix with 1 if the the two counties are adjacent or have a distance lower of 50 miles
for i in range(len(list_keys)):
  for j in range(len(list_keys)):

    if list_keys[j] in adj_dict[list_keys[i]] and ((list_keys[i], list_keys[j]) in db_distances or (list_keys[j], list_keys[i]) in db_distances):
      adj[i][j] = db_distances[(list_keys[i], list_keys[j])]

    else:
      if list_keys[i] == list_keys[j]:
        adj[i][j] = 0

      else:
        adj[i][j] = np.inf

In [19]:
adj_df = adj

# Convert adjacency matrix to a dataframe
# adj_df = pd.DataFrame(adj, columns = list_keys, index=list_keys)
# # Insert a new column with the fips of counties
# adj_df.insert(0, "--", list_keys, allow_duplicates=True)
# Export
# adj_df.to_csv('adjacency_matrix.csv', index=False)
# adj_df

viz =  pd.DataFrame(adj, columns = list_keys, index=list_keys)
viz.head()
# -------------- the matrix of distances is ready

1001   1003   1005       1007   1009       1011   1013       1015   \
1001   0.000000    inf    inf  43.403253    inf        inf    inf        inf   
1003        inf    0.0    inf        inf    inf        inf    inf        inf   
1005        inf    inf    0.0        inf    inf  24.265804    inf        inf   
1007  43.403253    inf    inf   0.000000    inf        inf    inf        inf   
1009        inf    inf    inf        inf    0.0        inf    inf  45.024731   

      1017   1019       1021   1023       1025   1027   1029       1031   \
1001    inf    inf  22.462994    inf        inf    inf    inf        inf   
1003    inf    inf        inf    inf  71.040281    inf    inf        inf   
1005    inf    inf        inf    inf        inf    inf    inf  47.190402   
1007    inf    inf  25.777246    inf        inf    inf    inf        inf   
1009    inf    inf        inf    inf        inf    inf    inf        inf   

      1033   1035       1037   1039   1041    1043       1045       1047   \
1001    inf    inf  35.892759    inf    inf     inf        inf  30.776371   
1003    inf    inf        inf    inf    inf     inf        inf        inf   
1005    inf    inf        inf    inf    inf     inf  32.684651        inf   
1007    inf    inf        inf    inf    inf     inf        inf  47.151920   
1009    inf    inf        inf    inf    inf  20.318        inf        inf   

      1049       1051       1053       1055   1057   1059   1061       1063   \
1001    inf  29.517585        inf        inf    inf    inf    inf        inf   
1003    inf        inf  46.843452        inf    inf    inf    inf        inf   
1005    inf        inf        inf        inf    inf    inf    inf        inf   
1007    inf        inf        inf        inf    inf    inf    inf  49.966138   
1009    inf        inf        inf  30.899196    inf    inf    inf        inf   

          1065       1067       1069   1071       1073   1075   1077   1079   \
1001        inf        inf        inf    inf        inf    inf    inf    inf   
1003        inf        inf        inf    inf        inf    inf    inf    inf   
1005        inf  26.303087  49.644778    inf        inf    inf    inf    inf   
1007  34.035146        inf        inf    inf  39.457361    inf    inf    inf   
1009        inf        inf        inf    inf  34.870901    inf    inf    inf   

      1081   1083       1085     1087   1089   1091   1093       1095   \
1001    inf    inf  26.844687      inf    inf    inf    inf        inf   
1003    inf    inf        inf      inf    inf    inf    inf        inf   
1005    inf    inf        inf  39.4421    inf    inf    inf        inf   
1007    inf    inf        inf      inf    inf    inf    inf        inf   
1009    inf    inf        inf      inf    inf    inf    inf  26.903026   

          1097       1099       1101       1103       1105   1107       1109   \
1001        inf        inf  34.493443        inf  38.460869    inf        inf   
1003  26.829363  67.163289        inf        inf        inf    inf        inf   
1005        inf        inf        inf        inf        inf    inf  31.884661   
1007        inf        inf        inf        inf  27.780451    inf        inf   
1009        inf        inf        inf  36.616229        inf    inf        inf   

      1111       1113       1115       1117   1119       1121   1123   \
1001    inf        inf        inf        inf    inf        inf    inf   
1003    inf        inf        inf        inf    inf        inf    inf   
1005    inf  31.658543        inf        inf    inf        inf    inf   
1007    inf        inf        inf  31.084953    inf        inf    inf   
1009    inf        inf  23.288948  49.778278    inf  47.668896    inf   

          1125       1127       1129   1131       1133   2013   2016   2020   \
1001        inf        inf        inf    inf        inf    inf    inf    inf   
1003        inf        inf  58.293342    inf        inf    inf    inf    inf   
1005        inf        inf        in

In [20]:
# # TODO: similarity matrix / connectivity 

# # ****************************************************************************
# # a) 
#     # weights = np.exp(-np.square(x / theta))

#     # https://scikit-learn.org/stable/modules/generated/sklearn.metrics.pairwise.rbf_kernel.html#sklearn.metrics.pairwise.rbf_kernel
#     # gaussian kernel: K(x, y) = exp(-gamma ||x-y||^2)


# temp = adj_df[adj_df == np.inf] = np.max(adj_df[adj_df != np.inf])
# g = temp.std()

g = 10

def gaussian_kernel(distance, gamma = g):
  return np.exp(-np.square(distance / gamma))

for i in range(len(list_keys)):
  for j in range(len(list_keys)):
    adj_df[i,j] = gaussian_kernel(adj_df[i,j])

adj_df


# ATTEMPT 1: rbf_kernel(xi, gamma=0.05) --> gaussian kernel with gamma = 0.05   --> low performances
# ATTEMPT 2: rbf_kernel(xi, gamma=0.05) --> gaussian kernel with gamma = 10
# ATTEMPT 3: rbf_kernel(xi, gamma=0.05) --> gaussian kernel with gamma = std (adj_df[adj_df == np.inf] = np.max(adj_df[adj_df != np.inf]) then adj_df.std())  --> low performances
# ATTEMPT 4: rbf_kernel(xi, gamma=0.05) --> gaussian kernel with gamma = 1

# # ****************************************************************************
# # c) directly use the geographical distances: actual distance between centroids of the counties if the two are adjacent, np.inf instead
# adj_df

array([[1., 0., 0., ..., 0., 0., 0.],
       [0., 1., 0., ..., 0., 0., 0.],
       [0., 0., 1., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 1., 0., 0.],
       [0., 0., 0., ..., 0., 1., 0.],
       [0., 0., 0., ..., 0., 0., 1.]])

In [21]:
# Convert adjacency matrix to a dataframe
adj_df = pd.DataFrame(adj_df, columns = list_keys, index=list_keys)
# # Insert a new column with the fips of counties
# adj_df.insert(0, "--", list_keys, allow_duplicates=True)
adj_df.head()

1001   1003   1005          1007   1009      1011   1013   \
1001  1.000000e+00    0.0    0.0  6.585316e-09    0.0  0.000000    0.0   
1003  0.000000e+00    1.0    0.0  0.000000e+00    0.0  0.000000    0.0   
1005  0.000000e+00    0.0    1.0  0.000000e+00    0.0  0.002772    0.0   
1007  6.585316e-09    0.0    0.0  1.000000e+00    0.0  0.000000    0.0   
1009  0.000000e+00    0.0    0.0  0.000000e+00    1.0  0.000000    0.0   

             1015   1017   1019      1021   1023          1025   1027   1029   \
1001  0.000000e+00    0.0    0.0  0.006436    0.0  0.000000e+00    0.0    0.0   
1003  0.000000e+00    0.0    0.0  0.000000    0.0  1.208835e-22    0.0    0.0   
1005  0.000000e+00    0.0    0.0  0.000000    0.0  0.000000e+00    0.0    0.0   
1007  0.000000e+00    0.0    0.0  0.001301    0.0  0.000000e+00    0.0    0.0   
1009  1.569884e-09    0.0    0.0  0.000000    0.0  0.000000e+00    0.0    0.0   

             1031   1033   1035      1037   1039   1041      1043      1045   \
1001  0.000000e+00    0.0    0.0  0.000003    0.0    0.0  0.000000  0.000000   
1003  0.000000e+00    0.0    0.0  0.000000    0.0    0.0  0.000000  0.000000   
1005  2.130827e-10    0.0    0.0  0.000000    0.0    0.0  0.000000  0.000023   
1007  0.000000e+00    0.0    0.0  0.000000    0.0    0.0  0.000000  0.000000   
1009  0.000000e+00    0.0    0.0  0.000000    0.0    0.0  0.016112  0.000000   

             1047   1049      1051          1053      1055   1057   1059   \
1001  7.698884e-05    0.0  0.000164  0.000000e+00  0.000000    0.0    0.0   
1003  0.000000e+00    0.0  0.000000  2.952820e-10  0.000000    0.0    0.0   
1005  0.000000e+00    0.0  0.000000  0.000000e+00  0.000000    0.0    0.0   
1007  2.209608e-10    0.0  0.000000  0.000000e+00  0.000000    0.0    0.0   
1009  0.000000e+00    0.0  0.000000  0.000000e+00  0.000071    0.0    0.0   

      1061          1063      1065      1067          1069   1071   \
1001    0.0  0.000000e+00  0.000000  0.000000  0.000000e+00    0.0   
1003    0.0  0.000000e+00  0.000000  0.000000  0.000000e+00    0.0   
1005    0.0  0.000000e+00  0.000000  0.000989  1.978614e-11    0.0   
1007    0.0  1.436610e-11  0.000009  0.000000  0.000000e+00    0.0   
1009    0.0  0.000000e+00  0.000000  0.000000  0.000000e+00    0.0   

             1073   1075   1077   1079   1081   1083      1085          1087   \
1001  0.000000e+00    0.0    0.0    0.0    0.0    0.0  0.000742  0.000000e+00   
1003  0.000000e+00    0.0    0.0    0.0    0.0    0.0  0.000000  0.000000e+00   
1005  0.000000e+00    0.0    0.0    0.0    0.0    0.0  0.000000  1.752955e-07   
1007  1.731975e-07    0.0    0.0    0.0    0.0    0.0  0.000000  0.000000e+00   
1009  5.236814e-06    0.0    0.0    0.0    0.0    0.0  0.000000  0.000000e+00   

      1089   1091   1093      1095      1097          1099      1101   \
1001    0.0    0.0    0.0  0.000000  0.000000  0.000000e+00  0.000007   
1003    0.0    0.0    0.0  0.000000  0.000748  2.566718e-20  0.000000   
1005    0.0    0.0    0.0  0.000000  0.000000  0.000000e+00  0.000000   
1007    0.0    0.0    0.0  0.000000  0.000000  0.000000e+00  0.000000   
1009    0.0    0.0    0.0  0.000719  0.000000  0.000000e+00  0.000000   

         1103          1105   1107      1109   1111      1113      1115   \
1001  0.000000  3.764863e-07    0.0  0.000000    0.0  0.000000  0.000000   
1003  0.000000  0.000000e+00    0.0  0.000000    0.0  0.000000  0.000000   
1005  0.000000  0.000000e+00    0.0  0.000038    0.0  0.000044  0.000000   
1007  0.000000  4.449563e-04    0.0  0.000000    0.0  0.000000  0.000000   
1009  0.000002  0.000000e+00    0.0  0.000000    0.0  0.000000  0.004411   

             1117   1119          1121   1123      1125          1127   \
1001  0.000000e+00    0.0  0.000000e+00    0.0  0.000000  0.000000e+00   
1003  0.000000e+00    0.0  0.000000e+00    0.0  0.000000  0.000000e+00   
1005  0.000000e+00    0.0  0.000000e+00    0.0  0.000000  0.000000e+00   
1007  6.360978e-05    0.0  0.000000e+

In [22]:
# TODO 2: record matrix

# path = "/Users/roccofelici/Desktop/GDL_project_COVID/dataset/"  # THIS LINE NEEDS TO BE CHANGED BASED ON THE PATH OF THE FILES TO RETRIEVE

# Import needed CSV for the dataset inlducing cases for day for fips
final_2020 = pd.read_csv(f"{path}final_df_2020.csv")
final_2021 = pd.read_csv(f"{path}final_df_2021.csv")
final_2022 = pd.read_csv(f"{path}final_df_2022.csv")

# Extrate information from dataframe and create a new dataframe with
# column = FIPS and row = Cases per Date
db = {}
for index, row in final_2020.iterrows():
  date = datetime.strptime(row['Date'], '%Y-%m-%d')
  db[(date, (row['FIPS']))] = row['Cases']
for index, row in final_2021.iterrows():
  date = datetime.strptime(row['Date'], '%Y-%m-%d')
  db[(date, (row['FIPS']))] = row['Cases']
for index, row in final_2022.iterrows():
  date = datetime.strptime(row['Date'], '%Y-%m-%d')
  db[(date, (row['FIPS']))] = row['Cases']

df_cases = pd.DataFrame(db.values(), index=pd.MultiIndex.from_tuples(db.keys())).unstack(1).fillna(0)[0]

In [23]:
# Convert the dataframe to a PandasDataset
dataset = PandasDataset(dataframe=df_cases,
              similarity_score="correntropy",
              temporal_aggregation="nearest")
dataset

PandasDataset(length=812, n_nodes=3220, n_channels=1)

In [24]:
# FIPS codes. Each node of the graph is defined as a county 
dataset.nodes

array([ 1001,  1003,  1005, ..., 78010, 78020, 78030])

In [25]:
# Create a tuple for the adjacency as the get_conncetivity of tsl
cols = adj_df.columns
bt = adj_df.apply(lambda x: x > 0)
adj_series = bt.apply(lambda x: list(cols[x.values]), axis=1)

adj_dict = adj_series.to_dict()
edge_index = [[], []]
edge_weight = []
for key in adj_dict:
  if key not in dataset.nodes:
    continue
  adj_fips = adj_dict[key]
  length = len(adj_fips)
  from_node = np.where(dataset.nodes == key)[0][0]
  for i in adj_fips:
    if int(i) in dataset.nodes:
      to_node = np.where(dataset.nodes == int(i))[0][0]
      edge_index[0].append(from_node)
      edge_index[1].append(to_node)
      edge_weight.append(1/length)

edge_index = np.array(edge_index)
edge_weight = np.array(edge_weight, dtype=np.float32)
adj = (edge_index, edge_weight)

In [26]:
# Create the torch dataset with the Spatio-Temporal dataset
torch_dataset = SpatioTemporalDataset(*dataset.numpy(return_idx=True),
                                      connectivity=adj,
                                      mask=dataset.mask,
                                      horizon=1, # number of steps to forecast: changed from 12 to one day
                                      window=15)  # 15 days period
print(torch_dataset)

SpatioTemporalDataset(n_samples=797, n_nodes=3220, n_channels=1)


In [34]:
# Create teh Data Module
scalers = {'data': StandardScaler(axis=(0, 1))}

splitter = dataset.get_splitter(val_len=0.1, test_len=0.2)

dm = SpatioTemporalDataModule(
    dataset=torch_dataset,
    scalers=scalers,
    splitter=splitter,
    batch_size=64,  
)

dm.setup()
print(dm)

SpatioTemporalDataModule(train_len=560, val_len=48, test_len=159, scalers=[data], batch_size=64)


In [35]:
# new added libraries 
from torch import nn
from einops import rearrange

from tsl.utils.parser_utils import ArgParser

from tsl.nn.blocks.encoders import ConditionalBlock
from tsl.nn.blocks.encoders.rnn import RNN

from tsl.nn.blocks.decoders.mlp_decoder import MLPDecoder

In [36]:
# # Create the class for the model
# class TimeThenSpaceModel(torch.nn.Module):
#     def __init__(self,
#                  input_size,
#                  hidden_size,
#                  rnn_layers,
#                  gcn_layers,
#                  horizon):
#         super(TimeThenSpaceModel, self).__init__()

#         self.input_encoder = torch.nn.Linear(input_size, hidden_size)

#         self.encoder = RNN(input_size=hidden_size,
#                            hidden_size=hidden_size,
#                            n_layers=rnn_layers)
        
#         self.decoder = GCNDecoder(
#             input_size=hidden_size,
#             hidden_size=hidden_size,
#             output_size=input_size,
#             horizon=horizon,
#             n_layers=gcn_layers)


#     def forward(self, x, edge_index, edge_weight):
#         x = self.input_encoder(x) # x: [batches steps nodes channels]
#         x = self.encoder(x, return_last_state=True)

#         return self.decoder(x, edge_index, edge_weight)

In [41]:

class RNNModel(nn.Module):
    def __init__(self,
                 input_size,
                 hidden_size,
                 horizon):
        super(RNNModel, self).__init__()

        self.input_encoder = nn.Sequential(
                nn.Linear(input_size, hidden_size),
                nn.ReLU()
            )

        self.rnn = RNN(input_size=hidden_size,
                       hidden_size=hidden_size,
                       n_layers=1)

        self.readout = MLPDecoder(
            input_size=hidden_size,
            hidden_size=hidden_size,
            output_size=input_size,
            horizon=horizon,
            n_layers=1)

    def forward(self, x, u=None, **kwargs):
        """"""
        # x: [batches steps nodes features]
        # u: [batches steps (nodes) features]
        if u is not None:
            if u.dim() == 3:
                u = rearrange(u, 'b s f -> b s 1 f')
            x = self.input_encoder(x, u)
        else:
            x = self.input_encoder(x)

        x = self.rnn(x, return_last_state=True)

        return self.readout(x)

In [69]:
# Create the predictor
metrics = {
    'mae': MaskedMAE(compute_on_step=False),
    'mape': MaskedMAPE(compute_on_step=False), # could be problematic for values near to zero
    'mae_at_7': MaskedMAE(compute_on_step=False, at=7), # 7 days ahead
    'mae_at_15': MaskedMAE(compute_on_step=False, at=15),
    'mae_at_31': MaskedMAE(compute_on_step=False, at=31),
    'mre': MaskedMRE(compute_on_step=False),              
    'mse': MaskedMSE(compute_on_step=False),
    }

model_kwargs = {
    'input_size': dm.n_channels,  # 1 channel
    'horizon': dm.horizon,  # 12, the number of steps ahead to forecast
    'hidden_size': 32
    }

# setup predictor
predictor = Predictor(
    model_class=RNNModel, # CHANGED: 
    model_kwargs=model_kwargs,
    optim_class=torch.optim.Adam,
    optim_kwargs={'lr': 0.001}, # compare 0.01, 0.001, 0.00001
    loss_fn=MaskedMRE(compute_on_step=True),  # loss function # try to change to MaskedMAE
    metrics=metrics
)

/usr/local/lib/python3.7/dist-packages/torchmetrics/utilities/prints.py:36: UserWarning: Torchmetrics v0.9 introduced a new argument class property called `full_state_update` that has
                not been set for this class (MaskedMAE). The property determines if `update` by
                default needs access to the full metric state. If this is not the case, significant speedups can be
                achieved and we recommend setting this to `False`.
                We provide an checking function
                `from torchmetrics.utilities import check_forward_no_full_state`
                that can be used to check if the `full_state_update=True` (old and potential slower behaviour,
                default for now) or if `full_state_update=False` can be used safely.
                
  warnings.warn(*args, **kwargs)
/usr/local/lib/python3.7/dist-packages/torchmetrics/utilities/prints.py:36: UserWarning: Torchmetrics v0.9 introduced a new argument class property called `full_s

In [70]:
# TRAIN THE DATA
logger = TensorBoardLogger(save_dir="logs", name="tsl_intro", version=0)

checkpoint_callback = ModelCheckpoint(
    dirpath='logs',
    save_top_k=1,
    monitor='val_mae',
    mode='min',
)

trainer = pl.Trainer(max_epochs=100,
                     logger=logger,
                     gpus=1 if torch.cuda.is_available() else None,
                     limit_train_batches=1000,
                     callbacks=[checkpoint_callback])

trainer.fit(predictor, datamodule=dm)

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
/usr/local/lib/python3.7/dist-packages/pytorch_lightning/callbacks/model_checkpoint.py:611: UserWarning: Checkpoint directory /content/logs exists and is not empty.
  rank_zero_warn(f"Checkpoint directory {dirpath} exists and is not empty.")
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name          | Type             | Params
---------------------------------------------------
0 | loss_fn       | MaskedMRE        | 0     
1 | train_metrics | MetricCollection | 0     
2 | val_metrics   | MetricCollection | 0     
3 | test_metrics  | MetricCollection | 0     
4 | model         | RNNModel         | 7.5 K 
---------------------------------------------------
7.5 K     Trainable params
0         Non-trainable params
7.5 K     Total params
0.030     Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/torchmetrics/utilities/prints.py:36: UserWarning: Torchmetrics v0.9 introduced a new argument class property called `full_state_update` that has
                not been set for this class (_ResultMetric). The property determines if `update` by
                default needs access to the full metric state. If this is not the case, significant speedups can be
                achieved and we recommend setting this to `False`.
                We provide an checking function
                `from torchmetrics.utilities import check_forward_no_full_state`
                that can be used to check if the `full_state_update=True` (old and potential slower behaviour,
                default for now) or if `full_state_update=False` can be used safely.
                
  warnings.warn(*args, **kwargs)
/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/trainer.py:1937: PossibleUserWarning: The number of training batches (8) is smaller than the 

Training: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

...

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]